In [10]:
import transformers
from datasets import load_dataset
import re

In [11]:
username = "Plim"  # change to your username
target_lang = "fr"

In [4]:
dataset = load_dataset("europarl_bilingual", lang1="en", lang2=target_lang, split="train")

Downloading:   0%|          | 0.00/2.60k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.6k [00:00<?, ?B/s]

Using custom data configuration en-fr-lang1=en,lang2=fr


Downloading:   0%|          | 0.00/142M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/140M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/9.30M [00:00<?, ?B/s]

0 examples [00:00, ? examples/s]

Dataset europarl_bilingual downloaded and prepared to /workspace/.cache/huggingface/datasets/europarl_bilingual/en-fr-lang1=en,lang2=fr/8.0.0/2ab0200e7729616bfd4a4df6bfb29b31746ceb5a59f8c75c02ca35e1ebead950. Subsequent calls will reuse this data.


In [12]:
def extract_text(batch):
    target_lang = "fr"
    chars_to_ignore_regex = '[^a-zàâäçéèêëîïôöùûüÿ\'’ ]'
    text = batch["translation"][target_lang]
    batch["text"] = re.sub(chars_to_ignore_regex, "", text.lower()).replace('’', "'")
    return batch

In [13]:
dataset = dataset.map(extract_text, remove_columns=dataset.column_names)

0ex [00:00, ?ex/s]

In [14]:
dataset.push_to_hub(f"{target_lang}_corpora_parliament_processed", split="train")

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

In [15]:
with open("text.txt", "w") as file:
    file.write(" ".join(dataset["text"]))

In [17]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
    has_added_eos = False
    for line in read_file:
        if not has_added_eos and "ngram 1=" in line:
            count=line.strip().split("=")[-1]
            write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
        elif not has_added_eos and "<s>" in line:
            write_file.write(line)
            write_file.write(line.replace("<s>", "</s>"))
            has_added_eos = True
        else:
            write_file.write(line)

In [1]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("./")

file ./config.json not found


OSError: Can't load config for './'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure './' is the correct path to a directory containing a config.json file